In [1]:
import concurrent.futures
from pathlib import Path
import os

from tqdm.auto import tqdm
from cs336_data import fast

In [6]:
fast.warc_gz_to_html_dir(
    warc_gz_path="../data/scrape/enwiki_urls_sampled_100k.warc.gz",
    html_dir="../data/scrape/warc_html",
    num_samples=32_000,
    min_content_length=fast.MIN_CONTENT_LENGTH,
    max_content_length=fast.MAX_CONTENT_LENGTH,
) 

In [5]:
html_dir = "../data/scrape/warc_html"
text_dir = "../data/scrape/warc_text"

In [6]:
html_paths = list(Path(html_dir).iterdir())

In [ ]:
for html_path in tqdm(html_paths):
    with open(html_path, "rb") as in_f:
        html_bytes = in_f.read()
    text = fast.html_bytes_to_text(html_bytes)
    text_path = f"{text_dir}/{html_path.name}"
    with open(text_path, "w") as out_f:
        out_f.write(text)

  0%|          | 0/32000 [00:00<?, ?it/s]

/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:63: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  return text
/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:63: XMLParsedAsHTMLWarning: It looks like you're parsing an XML document using an HTML parser. If this really is an HTML document (maybe it's XHTML?), you can ignore or filter this warning. If it's XML, you should know that using an XML parser will be more reliable. To parse this document as XML, make sure you have the lxml package installed, and pass the keyword argument `features="xml"` into the BeautifulSoup constructor.
  return text
/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:63: MarkupResemblesLocatorWarning: The input looks more like a URL than markup. You may want to use an HTTP client like requests to get the document behind the URL, and feed that document to Beauti

In [16]:
num_workers = len(os.sched_getaffinity(0))
num_workers

128

In [17]:
executor = concurrent.futures.ProcessPoolExecutor(max_workers=num_workers)

In [7]:
futures = []
for html_path in tqdm(html_paths):
    future = executor.submit(
        fast.html_bytes_to_text,
        html_path,
    )
    futures.append(future)

  0%|          | 0/32000 [00:00<?, ?it/s]

/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:65: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(html_bytes, "lxml")
/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:65: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(html_bytes, "lxml")
/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:65: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(html_bytes, "lxml")
/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:65: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle 

In [8]:
text_list = []
for future in tqdm(futures):
    text = future.result()
    text_list.append(text)

  0%|          | 0/32000 [00:00<?, ?it/s]

In [10]:
len(text_list)

32000

In [11]:
futures = []
for text in tqdm(text_list):
    future = executor.submit(
        fast.preprocess_for_fasttext,
        text,
    )
    futures.append(future)

  0%|          | 0/32000 [00:00<?, ?it/s]

In [12]:
ft_text_list = []
for future in tqdm(futures):
    ft_text = future.result()
    ft_text_list.append(ft_text)

  0%|          | 0/32000 [00:00<?, ?it/s]

In [13]:
ft_text_list

['media manipulation in young democracies : evidence from the 1989 brazilian presidential election - alexsandros cavgias , raphael corbi , luis meloni , lucas m . novaes , 2023 skip to main content intended for healthcare professionals close sign in create profile login failed . please check you entered the correct user name and password . sign in access personal subscriptions , purchases , paired institutional or society access and free tools such as email alerts and saved searches . required fields email : password : remember me forgotten your password ? sign in email : fields with * are mandatory already have an account ? login here search this journalsearch all journalsenter search terms . . . searchsearchenter search terms . . . searchsearch advanced search search access / profileaccessview access optionsview profilecreate profile cart 0 close drawer menuopen drawer menumenubrowse by discipline select discipline : all disciplines all disciplines health sciences life & biomedical s

In [14]:
with open("../data/pos.txt", "w") as out_f:
    for ft_text in tqdm(ft_text_list):
        line = f"__label__pos {ft_text}\n"
        out_f.write(line)

  0%|          | 0/32000 [00:00<?, ?it/s]

In [18]:
futures = []
html_paths = list(Path("../data/cc_neg").iterdir())
for html_path in tqdm(html_paths):
    future = executor.submit(
        fast.html_to_fasttext,
        html_path
    )
    futures.append(future)

  0%|          | 0/98524 [00:00<?, ?it/s]

/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:65: XMLParsedAsHTMLWarning: It looks like you're parsing an XML document using an HTML parser. If this really is an HTML document (maybe it's XHTML?), you can ignore or filter this warning. If it's XML, you should know that using an XML parser will be more reliable. To parse this document as XML, make sure you have the lxml package installed, and pass the keyword argument `features="xml"` into the BeautifulSoup constructor.
  soup = BeautifulSoup(html_bytes, "lxml")
/lfs/ampere2/0/ranjanr/cs336-a4/cs336-data/cs336_data/fast.py:65: XMLParsedAsHTMLWarning: It looks like you're parsing an XML document using an HTML parser. If this really is an HTML document (maybe it's XHTML?), you can ignore or filter this warning. If it's XML, you should know that using an XML parser will be more reliable. To parse this document as XML, make sure you have the lxml package installed, and pass the keyword argument `features="xml"` into the Beau

In [19]:
ft_text_list = []
for future in tqdm(futures):
    ft_text = future.result()
    ft_text_list.append(ft_text)

  0%|          | 0/98524 [00:00<?, ?it/s]

In [20]:
with open("../data/neg.txt", "w") as out_f:
    for ft_text in tqdm(ft_text_list):
        line = f"__label__neg {ft_text}\n"
        out_f.write(line)

  0%|          | 0/98524 [00:00<?, ?it/s]

In [24]:
fast.shuffle_balance_and_mix(["../data/pos.txt", "../data/neg.txt"], "../data/quality.txt")

In [28]:
fast.split_train_val("../data/quality.txt")

('../data/quality.train', '../data/quality.valid')

In [29]:
fast.train_fasttext("../data/quality.train", "../data/quality.valid", "../data/quality.bin")

Read 49M words
Number of words:  2594621
Number of labels: 2
Progress: 100.0% words/sec/thread:  262909 lr:  0.000000 avg.loss:  0.346690 ETA:   0h 0m 0s


(6400, 0.89421875, 0.89421875)